In [1]:
import matplotlib
%matplotlib tk
%autosave 180
%load_ext autoreload
%autoreload 2

import nest_asyncio
%config Completer.use_jedi = False

#
import matplotlib.pyplot as plt
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))


from cuml.cluster import HDBSCAN

import numpy as np
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt


from visualize import visualize


Autosaving every 180 seconds


In [2]:
data = np.load('/media/cat/4TB/donato/DON-006084/20210519/suite2p/plane0/binarized_traces.npz')
X = data['binarized_peak'].T

# 
pca = PCA(n_components=100)
X_pca = pca.fit_transform(X)

pc1 = 0
pcs = np.arange(pc1,pc1+3,1)
#pcs = np.arange(9,1)
X_pca = X_pca[:,pcs]
print (X_pca.shape)


(55740, 3)


In [19]:
###########################################
############ RUN GPU DBSCAN ###############
###########################################

min_duration = 30
model = HDBSCAN(
                min_cluster_size=min_duration, 
                gen_min_span_tree=True,
                cluster_selection_epsilon=0.05,
               )

# 
db = model.fit_predict(X_pca)

print (np.unique(db))
X_clean = X_pca.copy()

for k in range(np.max(db)):
    idx = np.where(db==k)[0]
    #print (k, idx.shape)
    # min duration 
    if idx.shape[0]<min_duration:
        
        X_clean = np.delete(X_clean, idx, axis=0)
        db = np.delete(db, idx, axis=0)

        
# remove noise clusters
idx = np.where(db==-1)[0]
print ("Noise shape: ", idx.shape)
X_clean = np.delete(X_clean, idx, axis=0)
db = np.delete(db, idx, axis=0)

# 
db_clean = db.copy()
ctr=0
rdn = np.arange(np.unique(db).shape[0])
rdn = np.random.choice(rdn,rdn.shape[0],replace=False)
for k in np.unique(db):
    idx = np.where(db==k)[0]
    db_clean[idx] = rdn[ctr]
    ctr+=1

Label prop iterations: 20
Label prop iterations: 9
Label prop iterations: 11
Label prop iterations: 6
Label prop iterations: 2
Iterations: 5
10784,143,1756,24,258,1556
Label prop iterations: 3
Iterations: 1
2019,48,311,8,57,107
[-1  0  1  2  3  4  5  6  7  8  9 10 11 12]
Noise shape:  (3216,)


In [20]:
###########################################
############ RUN GPU DBSCAN ###############
###########################################

print (X_clean.shape, db.shape)
v = visualize.Visualize()
fig = v.plot_scatter_3d( 
                       X_clean[:,:3], 
                       db_clean, 
                       'clusters',
                        'Edge',
                       1,1)
fig.show()

(52524, 3) (52524,)
